Папка на GDrive:

https://drive.google.com/drive/folders/1FeUwrVfxp09xAifiMngwtfrRZ8nhtj8T?usp=sharing


In [1]:
from os import listdir

USE_GDRIVE = False


if USE_GDRIVE:
    from google.colab import drive
    drive.mount("/home/GDrive")
    DATA_PATH = f"/home/GDrive/MyDrive/made_2021_fraud_project/data"
else:
    DATA_PATH = "../../data"

listdir(DATA_PATH)

['unlabeled',
 'good_data',
 'all_gps.csv',
 'all_accel.csv',
 'drivers_with_gps_and_sl_problems',
 'rides_of_drivers.csv']

In [2]:
# !pip install folium

In [3]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import folium

%matplotlib inline

In [4]:
def describe(df):
    display(pd.concat((df.dtypes, df.describe(datetime_is_numeric=True).T), axis=1))
    display(df.shape)

In [5]:
# [1, 0, None]
FORCE_FRAUD = 0

if FORCE_FRAUD == 1:
    driver_ids = listdir(f"{DATA_PATH}/drivers_with_gps_and_sl_problems")
    CUR_DRIVER = np.random.choice(driver_ids)
    CUR_PATH = f"{DATA_PATH}/drivers_with_gps_and_sl_problems/{CUR_DRIVER}"
    CUR_COLOR = "red"
elif FORCE_FRAUD == 0:
    driver_ids = listdir(f"{DATA_PATH}/good_data")
    CUR_DRIVER = np.random.choice(driver_ids)
    CUR_PATH = f"{DATA_PATH}/good_data/{CUR_DRIVER}"
    CUR_COLOR = "green"
else:
    driver_ids = listdir(f"{DATA_PATH}/unlabeled")
    CUR_DRIVER = np.random.choice(driver_ids)
    CUR_PATH = f"{DATA_PATH}/unlabeled/{CUR_DRIVER}"
    CUR_COLOR = "yellow"

display(CUR_DRIVER, CUR_PATH, CUR_COLOR)

'631642712709916337'

'../../data/good_data/631642712709916337'

'green'

In [6]:
df_gps = pd.read_csv(f"{CUR_PATH}/track.csv", parse_dates=[0, 3])
describe(df_gps)

0  count                           mean  \
time      datetime64[ns]  31776  2021-01-13 08:19:32.551705600   
lat              float64  31776                        55.6844   
lon              float64  31776                        37.7681   
gps_time  datetime64[ns]  31776  2021-01-13 08:19:31.819454720   

                          min                            25%  \
time      2021-01-12 09:18:41  2021-01-12 16:53:47.249999872   
lat                   55.4153                        55.6546   
lon                   37.4001                        37.6158   
gps_time  2021-01-12 09:18:41  2021-01-12 16:53:47.249999872   

                                 50%                            75%  \
time      2021-01-13 14:37:16.500000  2021-01-13 21:10:30.750000128   
lat                          55.6911                          55.74   
lon                          37.8397                        37.8782   
gps_time  2021-01-13 14:37:16.500000  2021-01-13 21:10:30.750000128   

                          max        std  
time      2021-01-14 02:59:00        NaN  
lat                   55.9007  0.0909471  
lon                   38.1199   0.165813  
gps_time  2021-01-14 02:59:00        NaN

(31776, 4)

In [7]:
df_accel = pd.read_csv(f"{CUR_PATH}/accelerometer.csv", parse_dates=[0])
describe(df_accel)

0   count       mean       std  \
time  datetime64[ns, pytz.FixedOffset(180)]     NaN        NaN       NaN   
x                                   float64  9991.0  -0.138711  0.938550   
y                                   float64  9991.0   9.226826  0.886553   
z                                   float64  9991.0   2.519474  1.080735   
lat                                 float64  9991.0  55.704197  0.082004   
lon                                 float64  9991.0  37.711455  0.163038   

            min        25%        50%        75%        max  
time        NaN        NaN        NaN        NaN        NaN  
x    -15.746719  -0.493866  -0.113190   0.254318   9.365463  
y     -7.385467   9.031586   9.309906   9.558601  12.608521  
z     -7.175796   2.026619   2.472839   2.895119  13.151581  
lat   55.415428  55.673192  55.710860  55.749492  55.910899  
lon   37.368640  37.580119  37.731358  37.851668  38.119785

(9991, 6)

In [8]:
df_accel["time"] = df_accel["time"].dt.tz_convert(None) + pd.DateOffset(hours=3)
describe(df_accel)

0 count                           mean  \
time  datetime64[ns]  9991  2015-12-28 17:43:58.362395904   
x            float64  9991                      -0.138711   
y            float64  9991                        9.22683   
z            float64  9991                        2.51947   
lat          float64  9991                        55.7042   
lon          float64  9991                        37.7115   

                             min                            25%  \
time  2015-12-27 03:00:02.423769  2015-12-27 19:49:35.038953984   
x                       -15.7467                      -0.493866   
y                       -7.38547                        9.03159   
z                        -7.1758                        2.02662   
lat                      55.4154                        55.6732   
lon                      37.3686                        37.5801   

                                50%                            75%  \
time  2015-12-28 10:58:41.665388032  2015-12-29 19:30:22.494980608   
x                          -0.11319                       0.254318   
y                           9.30991                         9.5586   
z                           2.47284                        2.89512   
lat                         55.7109                        55.7495   
lon                         37.7314                        37.8517   

                             max        std  
time  2015-12-30 11:52:24.716540        NaN  
x                        9.36546    0.93855  
y                        12.6085   0.886553  
z                        13.1516    1.08073  
lat                      55.9109  0.0820041  
lon                      38.1198   0.163038

(9991, 6)

In [9]:
center = (df_gps["lat"].mean(), df_gps["lon"].mean())
m = folium.Map(location=center, zoom_start=10)

fg = folium.FeatureGroup(name=f"gps").add_to(m)
folium.PolyLine(df_gps[["lat", "lon"]].values, color='black', weight=4, opacity=0.8).add_to(fg)

fg = folium.FeatureGroup(name=f"gps by time").add_to(m)
folium.PolyLine(df_gps.sort_values(by="time")[["lat", "lon"]].values, color='brown', weight=4, opacity=0.8).add_to(fg)

fg = folium.FeatureGroup(name=f"gps by gps_time").add_to(m)
folium.PolyLine(df_gps.sort_values(by="gps_time")[["lat", "lon"]].values, color='blue', weight=4, opacity=0.8).add_to(fg)

fg = folium.FeatureGroup(name=f"accel").add_to(m)
folium.PolyLine(df_accel[["lat", "lon"]].values, color='orange', weight=2, opacity=0.8).add_to(fg)

fg = folium.FeatureGroup(name=f"accel by time").add_to(m)
folium.PolyLine(df_accel.sort_values(by="time")[["lat", "lon"]].values, color=CUR_COLOR, weight=2, opacity=0.8).add_to(fg)

folium.map.LayerControl('topleft', collapsed= False).add_to(m)
display(m)

In [10]:
display(pd.merge(df_gps, df_accel, how="inner", on="time"))
display(pd.merge(df_gps, df_accel, how="inner", left_on="gps_time", right_on="time"))

Empty DataFrame
Columns: [time, lat_x, lon_x, gps_time, x, y, z, lat_y, lon_y]
Index: []

Empty DataFrame
Columns: [time_x, lat_x, lon_x, gps_time, time_y, x, y, z, lat_y, lon_y]
Index: []

Выводы:
- Показания GPS отсортированы по gps_time
- Колонка time в данных GPS не отсортирована по времени (пример '../../data/good_data/631642712709916337')
- Показания акселерометра не отсортированы по времени (почти всегда)
- Показания снимаются в разные интервалы времени